<a href="https://colab.research.google.com/github/palubad/gee-teaching-cuni/blob/main/python/Automatic_Forest_Cover_Classification.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Automatic Forest Cover classification using Sentinel-2 data and Machine Learning


Based on the article called [Automatic Classification of Forests using Sentinel-2 Multispectral Satellite Data and Machine Learning Methods in Google Earth Engine](http://www.actageographica.sk/stiahnutie/67_2_01_Onacilova_Kristofova_Paluba_final.pdf) by Onačillová K., Krištofová V., Paluba D.
<br> The tool for the JavaScript API can be found on [GitHub](https://github.com/palubad/Automatic-Forest-Classification-GEE).

In [1]:
# Author: Daniel Paluba
# EO4Landscape research group (eo4landscape.natur.cuni.cz)
# Department of applied geoinformatics and cartography
# Faculty of Science, Charles University, Prague, Czechia
#
# Copyright 2024 Daniel Paluba
#
# Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
#     https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

In [2]:
# import neccessary libraries
import ee                           # Earth Engine
import geemap                       # geemap library
import matplotlib.pyplot as plt     # for figure visualisation
import pandas as pd                 # for data storage and manipulation
from IPython.display import HTML    # to add custom HTML codes

## **Authentication**

Prior to using the Earth Engine Python client library, you need to authenticate (verify your identity) and use the resultant credentials to initialize the Python client. The following authentication flows should use a Cloud projects to authenticate, and they're used for unpaid (free, noncommercial) use as well as paid use. See the Earth Engine Authentication and Initialization guide for troubleshooting and to learn more.

In [3]:
ee.Authenticate()

## **Initialisation**

The initialization step verifies that valid credentials have been created and populates the Python client library with methods that the backend server supports.

---


**Here, you should add your GEE Cloud Project name.**

In [4]:
# Change PROJECT_NAME to your GEE Cloud Project name
ee.Initialize(project='PROJECT_NAME')

print('Welcome to the Earth Engine Python API!')

Welcome to the Earth Engine Python API!


In [ ]:
# Classic Python printing
print('Welcome to the Earth Engine Python API!')

# GEE Python API printing
print(ee.String('Welcome to the Earth Engine Python API!').getInfo())

Welcome to the Earth Engine Python API!
Welcome to the Earth Engine Python API!


In [37]:
# define the Map using the geemap library
Map = geemap.Map()

# Import and visualize the Map
display(Map)

# Draw your region of interest (ROI)
# QQQ

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

### Load the drawn region of interest from the Map

In [25]:
# Load the drawn region of interest from the Map
roi = ee.FeatureCollection(Map.draw_features)

# Or define it using Longitude and latitude coordinates
# roi = ee.Geometry.Point([longitude, latitude])

# inspect it
roi

In [26]:
# Code to remove drawn features from the Map. Uncomment if you want to use it.
# Map.remove_drawn_features()

# Or just remove the last drawing. Uncomment if you want to use it.
# Map.remove_last_drawn()

In [27]:
# Extend your area of interest with a buffer
study_area = roi.geometry().buffer(50000) # 50 km buffer in meters

### Import satellite imagery and filter it

In [28]:
# Filter the Sentinel-2 image collection
collection = (ee.ImageCollection('COPERNICUS/S2_SR_HARMONIZED')# Import data
      .filterBounds(study_area)                                    # Spatial filter
      .filterDate('2024-01-01', '2024-10-29')               # Temporal filter
      .filter(ee.Filter.lt('CLOUDY_PIXEL_PERCENTAGE', 30))  # Metadata filter
      .sort('CLOUDY_PIXEL_PERCENTAGE'))                     # Sort data

# Print data to the Console
display(dataset)

## Transform the JavaScript code to Python and use it

In [30]:
# Define the year of monitoring
year = 2024

# The intersection of CLC and GFC was adopted from Paluba et al. 2021 and further improved
# "Article": "https":#doi.Org/10.3390/rs13091743, "Codes": "https":#github.com/palubad/LC-SLIAC
# Create training data
gfc = ee.Image("UMD/hansen/global_forest_change_2022_v1_10")
CORINE = ee.Image("COPERNICUS/CORINE/V20/100m/2018").select('landcover')

# Create a forest mask for data
# Select pixels with >50% tree cover and mask out region with forest loss
# Tree cover from 2000
GFC2000 = gfc.select("treecover2000")

# Create a forest mask for data
# Select pixels with >50% tree cover and mask out region with forest loss
GFC2000_50 = GFC2000.updateMask(GFC2000.gte(50))

# Hansen Global forest - Select areas with forest loss from 2000 until the defined year of monitoring
forestLoss = gfc.select('lossyear')
lossMask = forestLoss.updateMask(forestLoss.gte(1).And(forestLoss.lte(ee.Number(year).subtract(ee.Number(2000)))))

# Apply the no-loss mask to the tree cover in 2000
maskedGFC = GFC2000_50.updateMask(lossMask.unmask().eq(0))

# Load the Copernicus Global Land Cover Layers and use only the selected land cover type
CORINE_forests = CORINE.updateMask(CORINE.eq(312).Or(CORINE.eq(311)).Or(CORINE.eq(313)))

# Create an intersection of these two land cover databases
CORINEAndHansen = CORINE_forests.updateMask(maskedGFC.select('treecover2000')).unmask()

# Create an intersection of these two land cover databases
CORINEAndHansenBinary = CORINEAndHansen.gt(0)

# Add the final intersection of CLC and GFC databases, based on which the training was performed
Map.addLayer(CORINEAndHansenBinary.clip(study_area).updateMask(CORINEAndHansenBinary.clip(study_area).eq(1)), {}, 'CLC&GFC forest mask')

input = collection.median().clip(study_area)

# Sample the input imagery to get a FeatureCollection of training data.
training =  input.addBands(CORINEAndHansenBinary).sample(

    numPixels=2000,
    seed=0,
    scale=10,
    region=study_area,
    tileScale=4
)

{'type': 'Image', 'bands': [{'id': 'landcover', 'data_type': {'type': 'PixelType', 'precision': 'int', 'min': -32768, 'max': 32767}, 'dimensions': [65000, 46000], 'crs': 'EPSG:3035', 'crs_transform': [100, 0, 900000, 0, -100, 5500000]}], 'version': 1578598451411424, 'id': 'COPERNICUS/CORINE/V20/100m/2018', 'properties': {'system:time_start': 1483228800000, 'landcover_class_names': ['Artificial surfaces; urban fabric; continuous urban fabric', 'Artificial surfaces; urban fabric; discontinuous urban fabric', 'Artificial surfaces; industrial, commercial, and transport units; industrial or commercial units', 'Artificial surfaces; industrial, commercial, and transport units; road and rail networks and associated land', 'Artificial surfaces; industrial, commercial, and transport units; port areas', 'Artificial surfaces; industrial, commercial, and transport units; airports', 'Artificial surfaces; mine, dump, and construction sites; mineral extraction sites', 'Artificial surfaces; mine, dump,

In [31]:
# Explore the distribution of input points
training.aggregate_histogram('landcover')

In [36]:
# Make a Random Forest classifier and train it.
classifier_RF = ee.Classifier.smileRandomForest(10) \
.train(
  features=training,
  classProperty='landcover',
  inputProperties=['B2','B3', 'B4','B8']
)

# Classify the input imagery.
classified_RF = input.select(['B2','B3', 'B4','B8']).classify(classifier_RF)

forest_Palette = [
'#30eb5b', # forest
]

# Load only forest
RF_forests = classified_RF.updateMask(classified_RF.eq(1))
Map.addLayer(RF_forests, {"palette": forest_Palette}, 'Classified forests')
Map

Map(bottom=11693.0, center=[47.98256841921405, 24.03401503901002], controls=(WidgetControl(options=['position'…